<a href="https://colab.research.google.com/github/mikeldiokelly/Project/blob/master/Mikeldi.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
import json
import requests
from google.colab import drive
import tarfile
import nltk
from nltk.stem import WordNetLemmatizer
import random

In [0]:
drive.mount('/content/drive')
!ls -alh "/content/drive/My Drive/WashingtonPost.v2.tar.gz"
!tar xvzf "/content/drive/My Drive/WashingtonPost.v2.tar.gz"
data_file='/content/drive/My Drive/WashingtonPost.v2.tar.gz'

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive
-rw------- 1 root root 1.6G Dec 12 19:33 '/content/drive/My Drive/WashingtonPost.v2.tar.gz'
WashingtonPost.v2/
WashingtonPost.v2/MD5SUMS
WashingtonPost.v2/README.md
WashingtonPost.v2/scripts/
WashingtonPost.v2/data/
WashingtonPost.v2/data/TREC_Washington_Post_collection.v2.jl
WashingtonPost.v2/scripts/wapo-print-docids.py
WashingtonPost.v2/scripts/wapo-docids-dupes
WashingtonPost.v2/scripts/wapo-remove-exact-duplicates.py


In [0]:
def get_full_content(doc):
  out_lst = list()
  for c in doc['contents']: 
    if 'content' in c:
      if type(c['content'])==str:
        out_lst.append(c['content'])
  return out_lst

In [0]:
def create_array(str):
  session = requests.Session()
  url = "https://en.wikipedia.org/w/api.php"
  params = {
    "action": "query",
    "format": "json",
    "titles": str,
    "prop": "links",
    "pllimit": "max"
  }

  response = session.get(url=url, params=params)
  data = response.json()
  pages = data["query"]["pages"]

  pg_count = 1
  array = []

  for key, val in pages.items():
    for link in val["links"]:
        array.append(link["title"])

  while "continue" in data:
    plcontinue = data["continue"]["plcontinue"]
    params["plcontinue"] = plcontinue

    response = session.get(url=url, params=params)
    data = response.json()
    pages = data["query"]["pages"]

    pg_count += 1

    for key, val in pages.items():
        for link in val["links"]:
            array.append(link["title"])
  return array

In [0]:
nfl_titles = create_array("National Football League")
football_titles = create_array("American football")
mlb_titles = create_array("Major League Baseball")
baseball_titles = create_array("Baseball")
nba_titles = create_array("National Basketball Association")
basketball_titles = create_array("Basketball")
nhl_titles = create_array("National Hockey League")
hockey_titles = create_array("Ice hockey")

with open('/content/WashingtonPost.v2/data/TREC_Washington_Post_collection.v2.jl') as fp:
   line = fp.readline()
   cnt = 1
   t_p = 0
   f_p = 0
   t_n = 0
   f_n = 0
   
   while line:
       counter=0
       counter_football=0
       counter_baseball=0
       counter_basketball=0
       counter_hockey=0
       doc = json.loads(line)
       d_long = ' '.join(get_full_content(doc))

       for key in nfl_titles:
        if (key in d_long):
          counter_football += 1
       for key in football_titles:
        if (key in d_long):
          counter_football += 1
          
       for key in mlb_titles:
        if (key in d_long):
          counter_baseball += 1
       for key in baseball_titles:
        if (key in d_long):
          counter_baseball += 1

       for key in nba_titles:
        if (key in d_long):
          counter_basketball += 1
       for key in basketball_titles:
        if (key in d_long):
          counter_basketball += 1

       for key in nhl_titles:
         if (key in d_long):
          counter_hockey += 1
       for key in hockey_titles:
         if (key in d_long):
          counter_hockey += 1

       counter=counter_football+counter_baseball+counter_basketball
       print ("\n")
       print("Line {}: {}".format(cnt, line.strip()))

       if (counter > 9):
         print ("Sports related article (Count =", counter, ")")
         print ("Count for each sport:")
         print ("Football:", counter_football)
         print ("Baseball:", counter_baseball)
         print ("Basketball:", counter_basketball)
         print ("Ice Hockey:", counter_hockey)

         if ("sports" in doc['article_url']):
           t_p+=1
           print ("True Positive")
         else:
           f_p+=1
           print ("False Positive")

       else:
        print ("Non sports related article (Count =", counter, ")")
        if ("sports" in doc['article_url']):
           f_n+=1
           print ("False Negative")
        else:
           t_n+=1
           print ("True Negative")

       line = fp.readline()
       cnt += 1
       if cnt > 500:
         break

print ("\n")
accuracy=(t_p+t_n)/(t_p+t_n+f_p+f_n)
precision=t_p/(t_p+f_p)
recall=t_p/(t_p+f_n)
f1=(2*t_p)/(2*t_p+f_p+f_n)
print("TP:", t_p)
print("FP:", f_p)
print("TN:", t_n)
print("FN:", f_n)
print("Accuracy = ", accuracy)
print("Precision = ", precision)
print("Recall = ", recall)
print("F1 score = ", f1)



Line 1: {"id": "b2e89334-33f9-11e1-825f-dabc29fd7071", "article_url": "https://www.washingtonpost.com/sports/colleges/danny-coale-jarrett-boykin-are-a-perfect-1-2-punch-for-virginia-tech/2011/12/31/gIQAAaW4SP_story.html", "title": "Danny Coale, Jarrett Boykin are a perfect 1-2 punch for Virginia Tech", "author": "Mark Giannotto", "published_date": 1325376562000, "contents": [{"content": "Colleges", "mime": "text/plain", "type": "kicker"}, {"content": "Danny Coale, Jarrett Boykin are a perfect 1-2 punch for Virginia Tech", "mime": "text/plain", "type": "title"}, {"fullcaption": "Virginia Tech wide receiver Danny Coale (19) was lightly recruited out of Episcopal in Alexandria but has teamed with Jarrett Boykin for a record-breaking receiving duo. (John Bazemore/AP)", "imageURL": "https://img.washingtonpost.com/rw/2010-2019/WashingtonPost/2011/11/12/Sports/Images/Virginia_Tech_Georgia_Tech_Football_0cf3f.jpg", "mime": "image/jpeg", "imageHeight": 2260, "imageWidth": 2775, "type": "image